# Importation and Initialisation

In [1]:
import time
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
# from firebase import FirebaseManager 
from mongo import MongoDBManager
from selenium.webdriver.common.keys import Keys
import os
from dotenv import load_dotenv
from tqdm.notebook import tqdm

In [2]:
collection_names=["professions_by_field","posts_by_profession","posts_by_profession_by_language"]
# credential_path="./indeedrecommender-firebase.json"
# firebase_manager=FirebaseManager(credential_path)

In [3]:
load_dotenv()
uri = os.getenv('MONGODB_URI')
database_name = os.getenv('DATABASE_NAME')
mongo_manager = MongoDBManager(uri, database_name)

# Retrieve Fields and theirs professions from Ulaval Website

In [15]:
def retrieve_professions_from_field_first(field):
    """
    Retrieves professions from the field using the provided field parameter.

    Args:
        field (str): The field to retrieve professions from.

    Raises:
        Exception: If no elements are found for the first function for the given field.

    Returns:
        None
    """
    global datas
    h3_elements = driver.find_elements(By.XPATH, "//h3[contains(text(), 'Professions')]")
    print(h3_elements)
    if len(h3_elements)==0:
        raise Exception(f"Aucun element trouvé pour la première fonction pour {field}")
    for h3_element in h3_elements:
        ul_element = h3_element.find_element(By.XPATH, "following-sibling::ul")
        driver.execute_script("arguments[0].scrollIntoView(true);", h3_element)
        if ul_element:
            li_elements = ul_element.find_elements(By.XPATH, "./li")
            for element in li_elements:
                text = driver.execute_script("return arguments[0].innerText;", element)
                # print(text)
                if text not in datas[field]:
                    datas[field].append(text)
            # print(datas)
        time.sleep(0.5)
    # driver.back()



def retrieve_professions_from_field_second(field):
    """
    Retrieves professions from the second field.

    Args:
        field (str): The field to retrieve professions from.

    Raises:
        Exception: If no elements are found for the second function for the given field.

    Returns:
        None
    """
    global datas
    strong_elements = driver.find_elements(By.XPATH, "//p[strong[contains(text(), 'Professions')]]")
    print(f"strong: {strong_elements}")
    if len(strong_elements)==0:
        errors.append(field)
        raise Exception(f"Aucun element trouvé pour la deuxième fonction pour {field}")
    for strong_element in strong_elements:
        ul_element = strong_element.find_element(By.XPATH, "following-sibling::ul")
        if ul_element:
            driver.execute_script("arguments[0].scrollIntoView(true);", ul_element)
            li_elements = ul_element.find_elements(By.XPATH, "./li")
            for element in li_elements:
                text = driver.execute_script("return arguments[0].innerText;", element)
                # ##################print(text)
                if text not in datas[field]:
                    datas[field].append(text)
            # print(datas)
        time.sleep(0.5)
    # driver.back()

def retrieve_professions_from_field(field):
    global nb_of_functions_tried, nb_of_functions
    try:
        if nb_of_functions_tried==1:
            retrieve_professions_from_field_first(field)
            driver.back()
        if nb_of_functions_tried==2:
            retrieve_professions_from_field_second(field)
            driver.back()
            nb_of_functions_tried=1
    except Exception as e:
        print(e)
        nb_of_functions_tried+=1
        retrieve_professions_from_field(field)

    if nb_of_functions_tried > nb_of_functions:
        driver.back()
        nb_of_functions_tried=1
    return



In [17]:
driver = webdriver.Chrome()
driver.get("https://www.ulaval.ca/etudes/programmes")
title = driver.title

# Keys represente fields and values are arrays whose contains professions 
datas={}
errors=[]
nb_of_functions=2
nb_of_functions_tried=1

pagination_next_element=driver.find_element(By.ID,"pagination-heading").find_element(By.XPATH, "following-sibling::ul").find_element(By.XPATH, "./li[@class='pagination-item pagination-item--suivant']")
print(pagination_next_element)
while pagination_next_element:
    results_element= driver.find_element(By.ID,"resultats")
    children=results_element.find_elements(By.XPATH, "./ul[@class='views-row']")

    for child in children:
        element=child.find_element(By.XPATH, "./li/a")
        field=element.find_element(By.XPATH,"./div[@class='main-info']/h3[@class='titre-programme']").text
        if field not in datas:
            datas[field]=[]     
        driver.execute_script("arguments[0].scrollIntoView(true);", element)
        time.sleep(0.5)
        driver.execute_script("arguments[0].click();", element)
        retrieve_professions_from_field(field)
    
    driver.execute_script("arguments[0].scrollIntoView(true);", pagination_next_element)
    time.sleep(0.5)
    driver.execute_script("arguments[0].click();", pagination_next_element.find_element(By.TAG_NAME, "a"))
    try:
        pagination_next_element=driver.find_element(By.ID,"pagination-heading").find_element(By.XPATH, "following-sibling::ul").find_element(By.XPATH, "./li[@class='pagination-item pagination-item--suivant']")
    except Exception as e:
        pagination_next_element=None
   
driver.close()
print(datas)


<selenium.webdriver.remote.webelement.WebElement (session="2f53a94b5b665b178f9370d39bd38c0a", element="f.C3B6162583B631E5C0C3845834FC0917.d.C863EDD6A306AD0AD820AA41C2E0F306.e.78")>
[<selenium.webdriver.remote.webelement.WebElement (session="2f53a94b5b665b178f9370d39bd38c0a", element="f.C3B6162583B631E5C0C3845834FC0917.d.A9DF1AA0C677CB9DA4C79B281A949297.e.113")>]
[]
Aucun element trouvé pour la première fonction pour administration des affaires
strong: [<selenium.webdriver.remote.webelement.WebElement (session="2f53a94b5b665b178f9370d39bd38c0a", element="f.C3B6162583B631E5C0C3845834FC0917.d.69E6A3BF5BB5EE934B62C2F73EE8429B.e.145")>, <selenium.webdriver.remote.webelement.WebElement (session="2f53a94b5b665b178f9370d39bd38c0a", element="f.C3B6162583B631E5C0C3845834FC0917.d.69E6A3BF5BB5EE934B62C2F73EE8429B.e.146")>, <selenium.webdriver.remote.webelement.WebElement (session="2f53a94b5b665b178f9370d39bd38c0a", element="f.C3B6162583B631E5C0C3845834FC0917.d.69E6A3BF5BB5EE934B62C2F73EE8429B.e.14

NoSuchWindowException: Message: no such window: target window already closed
from unknown error: web view not found
  (Session info: chrome=127.0.6533.120)
Stacktrace:
	GetHandleVerifier [0x00007FF6183A9642+30946]
	(No symbol) [0x00007FF61835E3D9]
	(No symbol) [0x00007FF618256FDA]
	(No symbol) [0x00007FF61822CB85]
	(No symbol) [0x00007FF6182D37A7]
	(No symbol) [0x00007FF6182EA771]
	(No symbol) [0x00007FF6182CC813]
	(No symbol) [0x00007FF61829A6E5]
	(No symbol) [0x00007FF61829B021]
	GetHandleVerifier [0x00007FF6184DF84D+1301229]
	GetHandleVerifier [0x00007FF6184EBDC7+1351783]
	GetHandleVerifier [0x00007FF6184E2A13+1313971]
	GetHandleVerifier [0x00007FF6183DDD16+245686]
	(No symbol) [0x00007FF61836759F]
	(No symbol) [0x00007FF618363814]
	(No symbol) [0x00007FF6183639A2]
	(No symbol) [0x00007FF61835A3FF]
	BaseThreadInitThunk [0x00007FF91B93257D+29]
	RtlUserThreadStart [0x00007FF91C26AF28+40]


In [5]:
for key in datas.keys():
    mongo_manager.add_data_to_mongodb(collection_names[0],key,{"professions":datas[key]})


Data added to professions_by_field/actuariat
Data added to professions_by_field/actuariat - avec mémoire
Data added to professions_by_field/administration des affaires
Data added to professions_by_field/administration des affaires - Global Business
Data added to professions_by_field/administration des affaires - analytique d'affaires
Data added to professions_by_field/administration des affaires - audit interne, contrôle et gestion des risques
Data added to professions_by_field/administration des affaires - chaînes de blocs pour gestionnaires
Data added to professions_by_field/administration des affaires - communication marketing sur les nouveaux médias
Data added to professions_by_field/administration des affaires - comptabilité
Data added to professions_by_field/administration des affaires - comptabilité et décisions d'affaires
Data added to professions_by_field/administration des affaires - comptabilité pour gestionnaires
Data added to professions_by_field/administration des affaire

# Retrieve Posts from Indeed

In [18]:
import re
from datetime import datetime
from dateutil.relativedelta import relativedelta

def stateDateToDate(stateDate):
   """
   Converts a state date string into a datetime object.
   Parameters:
   stateDate (str): The state date string to be converted.
   Returns:
   datetime: The converted datetime object.
   """

   date=None
   value=None
   for str in stateDate.split(" "):
      try:
         date= datetime.strptime(str, '%Y-%m-%d')
      except Exception as e:
         date=None
      
      if date:
         return date
   try:
      match = re.search(r'\d+', stateDate)
      if match:
         value= int(match.group())
   except Exception as e:
      e

   if value:
      if bool(re.compile(r'\b(\w*jour\w*|\w*day\w*)\b', re.IGNORECASE).search(stateDate)):
         date= (datetime.now()-relativedelta(days=value)).strftime('%Y-%m-%d')
      if bool(re.compile(r'\b(\w*mois\w*|\w*month\w*)\b', re.IGNORECASE).search(stateDate)):
         date= (datetime.now()-relativedelta(months=value)).strftime('%Y-%m-%d')
      if bool(re.compile(r'\b(\w*an \w*|\w*year\w*|\w*année\w*)\b', re.IGNORECASE).search(stateDate)):
         date= (datetime.now()-relativedelta(years=value)).strftime('%Y-%m-%d')
      if bool(re.compile(r'\b(\w*now\w*|\w*maintenant\w*|\w*instant\w*)\b', re.IGNORECASE).search(stateDate)):
         date= (datetime.now()).strftime('%Y-%m-%d')            
   return date

In [19]:
positionsDetailsList = {}

def indeedPositionInfos(profession, country,language):
    """
    Retrieves position details from Indeed job listings.
    Args:
        profession (str): The profession to search for.
    Returns:
        None
    Raises:
        None
    """
    global positionsDetailsList
    positionsDetails={}
    positionTitle=''
    companyName=''
    location=''
    jobType=''
    jobType2=''
    jobType3=''
    jobType4=''
    jobBenefits=[]
    benefits=''
    shiftAndSchedule=''
    description=''
    positionPostedDate=''
    postedText=''
    salary=''
    try:
        positionsDescriptionList = driver.find_element(By.XPATH, "//div[@id='mosaic-provider-jobcards']")
        ulElement = positionsDescriptionList.find_element(By.XPATH, "./ul")
        liElements = ulElement.find_elements(By.XPATH, "./li[@class='css-5lfssm eu4oa1w0']")
    except Exception as e:
        liElements=[]
    for li in liElements:
        positionsDetails = {}
        driver.execute_script("arguments[0].scrollIntoView(true);", li)
        time.sleep(0.5)
        try:
          position=li.find_element(By.XPATH, ".//h2[contains(@class, 'jobTitle')]/a")
          positionTitle = driver.execute_script("return arguments[0].innerText;", position)
        #   print(positionTitle)
        except Exception as e:
            # print("No position found")
            position=None

        try:
          dateElement=li.find_element(By.XPATH, ".//span[@data-testid='myJobsStateDate']")
          postedText=driver.execute_script("return arguments[0].innerText.replace('Posted', '').trim().replace(/\\n/g, ' ');", dateElement)
          positionPostedDate=stateDateToDate(postedText)
        except Exception as e:
            # print("No Date found")
            dateElement=None
        
        if position :
            driver.execute_script("arguments[0].click();", position)
            time.sleep(0.5)
            try:
               positionsDetailsElement = driver.find_element(By.XPATH, "//div[@id='jobsearch-ViewjobPaneWrapper']")
            except Exception as e:
               positionsDetailsElement=None
            #    print("No position details found")
               
            
            if positionsDetailsElement:	
                try:
                    companyName = driver.execute_script("return arguments[0].innerText;",positionsDetailsElement.find_element(By.XPATH, ".//div[@data-testid='inlineHeader-companyName']"))
                except Exception as e:
                    # print("No company name found")
                    companyName=''
                try:
                    location = driver.execute_script("return arguments[0].innerText;",positionsDetailsElement.find_element(By.XPATH, ".//div[@data-testid='inlineHeader-companyLocation']"))
                except Exception as e:  
                    # print("No location found")
                    location=''
                try:
                    jobType = driver.execute_script("return arguments[0].innerText;",positionsDetailsElement.find_element(By.ID, "salaryInfoAndJobType"))
                    # print(F"JOB type: {jobType}")
                except Exception as e:
                    # print("No job type found")
                    jobType=''
                try:
                    jobType2 = driver.execute_script("return arguments[0].innerText;",positionsDetailsElement.find_element(By.ID,"jobDetailsSection").find_element(By.XPATH, ".//div[@data-testid='Permanent-tile']"))
                    # print(F"JOB type 2: {jobType2}")
                except Exception as e:
                    # print("No job type 2 found")
                    jobType2=""
                try:
                    jobType3 = driver.execute_script("return arguments[0].innerText;",positionsDetailsElement.find_element(By.XPATH, ".//div[@data-testid='Full-time-tile']"))
                    # print(F"JOB type 3: {jobType3}")
                except Exception as e:
                    # print("No job type 3 found")
                    jobType3=""
                try:
                    jobType4 = driver.execute_script("return arguments[0].innerText;",positionsDetailsElement.find_element(By.XPATH, ".//div[@data-testid='Part-time-tile']"))
                    # print(F"JOB type 4: {jobType4}")
                except Exception as e:
                    # print("No job type 4 found")
                    jobType4=""
                
                if re.search(r'-', jobType):
                    salary = jobType.split("-")[0]
                    jobType= jobType.split("-")[1]
                # print(F"Salary: {salary}")
                jobType=jobType.replace(salary,'')
                # print(F"JOB type: {jobType}")
                jobType=jobType.split(",")
                if jobType2 not in jobType:
                    jobType.append(jobType2)
                if jobType3 not in jobType:
                    jobType.append(jobType3)
                if jobType4 not in jobType:
                    jobType.append(jobType4)
                jobType.remove('')
                try:
                    shiftAndSchedule = driver.execute_script("return arguments[0].innerText;",positionsDetailsElement.find_element(By.XPATH,".//h3[contains(text(), 'Quart de travail et horaire')]").find_element(By.XPATH, "following-sibling::div"))
                    # print(F"Shift and schedule: {shiftAndSchedule}")
                except Exception as e:
                    # print("No shift and schedule found")
                    shiftAndSchedule=''
                jobBenefits = []
                try:
                    benefits = positionsDetailsElement.find_elements(By.XPATH, ".//div[@id='benefits']/div/div/span/ul[@class='css-8tnble eu4oa1w0']/li")
                    for benefit in benefits:
                        jobBenefits.append(driver.execute_script("return arguments[0].innerText;",benefit))
                
                except Exception as e:
                    # print("No benefits found")
                    benefits=''
                    
                try:
                    description = driver.execute_script("return arguments[0].innerText;",positionsDetailsElement.find_element(By.XPATH, ".//div[@id='jobDescriptionText']"))
                except Exception as e:
                    # print("No description found")
                    description=''
        
        positionsDetails["positionTitle"]=positionTitle
        positionsDetails["companyName"]=companyName
        positionsDetails["location"]=location
        positionsDetails["jobType"]=jobType
        positionsDetails["description"]=description
        positionsDetails["datePosted"]=positionPostedDate
        positionsDetails["salary"]=salary
        positionsDetails["shiftAndSchedule"]=shiftAndSchedule
        positionsDetails["jobBenefits"]=jobBenefits
        if country not in positionsDetailsList:
            positionsDetailsList[country]={}
        if profession not in positionsDetailsList[country]:
            positionsDetailsList[country][profession]={}
        if language not in positionsDetailsList[country][profession]:
            positionsDetailsList[country][profession][language]=[]
        positionsDetailsList[country][profession][language].append(positionsDetails)
        time.sleep(2)


In [20]:
professions_by_field=mongo_manager.read_all_documents_in_collection(collection_names[0])
print(professions_by_field)
professions=[]
for key in professions_by_field.keys():
    professions.extend(professions_by_field[key]["professions"])
print(professions)

{'actuariat': {'_id': 'actuariat', 'professions': ['Actuaire', 'Analyste de marché', 'Analyste en assurances', 'Analyste en placements', 'Analyste en finance']}, 'actuariat - avec mémoire': {'_id': 'actuariat - avec mémoire', 'professions': []}, 'administration des affaires': {'_id': 'administration des affaires', 'professions': ["Agente ou agent d'administration", "Chargée ou chargé de développement d'affaires", 'Directrice administrative ou directeur administratif', 'Gestionnaire', 'Chargée ou chargé de projet', 'Cheffe ou chef de service ou de division', 'Consultante ou consultant', 'Gestionnaire/décideuse ou décideur', 'Experte ou expert en science des données (data scientist)', "Analyste en gestion de l'actif", 'Analyste financière ou analyste financier', 'Conseillère ou conseiller en gestion budgétaire et financière', 'Conseillère ou conseiller en placement', 'Courtière ou courtier en valeurs mobilières', 'Gestionnaire de portefeuille', 'Gestionnaire de risques (CRM)', 'Négociatr

In [21]:
countries=["Canada","US","France"]
languages=["fr","en"]

In [22]:
import random
from selenium.webdriver.chrome.options import Options


USER_AGENTS = [
    "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/123.0.0.0 Safari/537.36",
    "Mozilla/5.0 (Windows NT 10.0; Win64; x64; rv:124.0) Gecko/20100101 Firefox/124.0",
    "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/123.0.0.0 Safari/537.36 Edg/123.0.2420.81",
    "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/123.0.0.0 Safari/537.36 OPR/109.0.0.0",
    "Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/123.0.0.0 Safari/537.36",
    "Mozilla/5.0 (Macintosh; Intel Mac OS X 14.4; rv:124.0) Gecko/20100101 Firefox/124.0",
    "Mozilla/5.0 (Macintosh; Intel Mac OS X 14_4_1) AppleWebKit/605.1.15 (KHTML, like Gecko) Version/17.4.1 Safari/605.1.15",
    "Mozilla/5.0 (Macintosh; Intel Mac OS X 14_4_1) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/123.0.0.0 Safari/537.36 OPR/109.0.0.0",
    "Mozilla/5.0 (X11; Linux x86_64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/123.0.0.0 Safari/537.36",
    "Mozilla/5.0 (X11; Linux i686; rv:124.0) Gecko/20100101 Firefox/124.0",
]

# def get_random_proxy():
#     return random.choice(PROXIES)


chrome_options = Options()
chrome_options.add_argument("--disable-blink-features=AutomationControlled")
chrome_options.add_argument(f'user-agent={random.choice(USER_AGENTS)}')


def random_sleep(min_time=1, max_time=5):
    time.sleep(random.uniform(min_time, max_time))

def indeedDataFill(ulavalPosition, location):
    if location=="Canada":
        driver.get(f"https://emplois.ca.indeed.com/jobs?q={ulavalPosition.replace(' ','+')}&l={location.replace(' ','+')}")
    if location=="US":
        driver.get(f"https://www.indeed.com/jobs?q={ulavalPosition.replace(' ','+')}&l={location.replace(' ','+')}")
    if location=="France":
        driver.get(f"https://www.indeed.fr/jobs?q={ulavalPosition.replace(' ','+')}&l={location .replace(' ','+')}")    
    random_sleep()
    # try:
    #     title_input = driver.find_element(By.ID, 'text-input-what')
    #     location_input = driver.find_element(By.ID, 'text-input-where')
    # except Exception as e:
    #     e
    # if title_input:
    #     driver.execute_script("arguments[0].value = '';", title_input)
    #     # driver.execute_script("arguments[0].value = '';", location_input)
    #     # location_input.send_keys(location)
    #     title_input.send_keys(ulavalPosition, Keys.RETURN)
    # return title_input, location_input
    

In [23]:
import requests

def translate_text(text, target_language):
    url = "https://api.mymemory.translated.net/get"
    params = {
        'q': text,
        'langpair': f'fr|{target_language}'  # Exemple pour traduire du français vers l'anglais
    }
    response = requests.get(url, params=params)
    return response.json().get('responseData', {}).get('translatedText')

def traduction(profession, language):
    if language=="fr":
        return profession
    if language=="en":
        return translate_text(profession, "en")
    
traduction("Infirmier", "en")

'Nurse'

In [25]:
try:
    driver = webdriver.Chrome(options=chrome_options)
    for profession in tqdm(professions[:14], desc=f"Professions: ",leave=False):
        print(profession)
        for country in tqdm(countries, desc=f"Countries: ",leave=True):
            for language in tqdm(languages, desc=f"Languages: ",leave=True):
                indeedDataFill(traduction(profession,language), country)
                try:
                    
                    pagination_next_element=driver.find_element(By.XPATH, "//nav/ul/li/a[@data-testid='pagination-page-next']")
                except Exception as e:
                    pagination_next_element=None
                    


                if not pagination_next_element: 
                    print(f"Boutton {pagination_next_element}")
                    indeedPositionInfos(profession, country,language)
                if pagination_next_element:
                    while pagination_next_element:
                        indeedPositionInfos(profession, country,language)
                        if pagination_next_element:
                            driver.execute_script("arguments[0].click();", pagination_next_element)
                        try:
                            pagination_next_element=driver.find_element(By.XPATH, "//nav/ul/li/a[@data-testid='pagination-page-next']")
                        except Exception as e:
                            pagination_next_element=None
            
    driver.close()
except Exception as e:
    print(e)
    driver.close()

Professions:   0%|          | 0/14 [00:00<?, ?it/s]

Actuaire


Countries:   0%|          | 0/3 [00:00<?, ?it/s]

Languages:   0%|          | 0/2 [00:00<?, ?it/s]

Boutton None
Boutton None


...

Languages:   0%|          | 0/2 [00:00<?, ?it/s]

Boutton None
Boutton None


Languages:   0%|          | 0/2 [00:00<?, ?it/s]

Message: no such window: target window already closed
from unknown error: web view not found
  (Session info: chrome=127.0.6533.120)
Stacktrace:
	GetHandleVerifier [0x00007FF6183A9642+30946]
	(No symbol) [0x00007FF61835E3D9]
	(No symbol) [0x00007FF618256FDA]
	(No symbol) [0x00007FF61822CB85]
	(No symbol) [0x00007FF6182D37A7]
	(No symbol) [0x00007FF6182EA771]
	(No symbol) [0x00007FF6182CC813]
	(No symbol) [0x00007FF61829A6E5]
	(No symbol) [0x00007FF61829B021]
	GetHandleVerifier [0x00007FF6184DF84D+1301229]
	GetHandleVerifier [0x00007FF6184EBDC7+1351783]
	GetHandleVerifier [0x00007FF6184E2A13+1313971]
	GetHandleVerifier [0x00007FF6183DDD16+245686]
	(No symbol) [0x00007FF61836759F]
	(No symbol) [0x00007FF618363814]
	(No symbol) [0x00007FF6183639A2]
	(No symbol) [0x00007FF61835A3FF]
	BaseThreadInitThunk [0x00007FF91B93257D+29]
	RtlUserThreadStart [0x00007FF91C26AF28+40]



WebDriverException: Message: disconnected: not connected to DevTools
  (failed to check if window was closed: disconnected: not connected to DevTools)
  (Session info: chrome=127.0.6533.120)
Stacktrace:
	GetHandleVerifier [0x00007FF6183A9642+30946]
	(No symbol) [0x00007FF61835E3D9]
	(No symbol) [0x00007FF618256FDA]
	(No symbol) [0x00007FF61823DB35]
	(No symbol) [0x00007FF61823E46F]
	(No symbol) [0x00007FF6182575F3]
	(No symbol) [0x00007FF61822C67D]
	(No symbol) [0x00007FF6182DA7C1]
	(No symbol) [0x00007FF6182CCA30]
	(No symbol) [0x00007FF61829A6E5]
	(No symbol) [0x00007FF61829B021]
	GetHandleVerifier [0x00007FF6184DF84D+1301229]
	GetHandleVerifier [0x00007FF6184EBDC7+1351783]
	GetHandleVerifier [0x00007FF6184E2A13+1313971]
	GetHandleVerifier [0x00007FF6183DDD16+245686]
	(No symbol) [0x00007FF61836759F]
	(No symbol) [0x00007FF618363814]
	(No symbol) [0x00007FF6183639A2]
	(No symbol) [0x00007FF61835A3FF]
	BaseThreadInitThunk [0x00007FF91B93257D+29]
	RtlUserThreadStart [0x00007FF91C26AF28

In [19]:
for country in tqdm(positionsDetailsList.keys()):
    for profession in tqdm(positionsDetailsList[country].keys()):
        for language in tqdm(positionsDetailsList[country][profession].keys()):
            mongo_manager.add_data_to_mongodb(collection_names[2],country,{profession:positionsDetailsList[country][profession][language]})

  0%|          | 0/2 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

Document data: {'_id': 'Canada', 'Analyste financière ou analyste financier': {'fr': [{'positionTitle': 'Analyste financier', 'companyName': 'QSL Canada inc.', 'location': 'Ville de Québec, QC•Travail hybride', 'jobType': ['Permanent', ' Temps plein'], 'description': "Poste convoité : Analyste financier\n\nPOSTE ANALYSTE FINANCIER\n\nPartie intégrante de l’équipe des finances et de la comptabilité, vous aurez comme principale responsabilité d’analyser la performance financière et opérationnelle des différentes compagnies, divisions et terminaux du groupe. Vous serez également responsable de concevoir des indicateurs de performance et des rapports pour les différents départements de l’entreprise. Partenaire et expert dans votre domaine, votre travail aura un impact sur le quotidien de nos processus opérationnels et financiers.\n\nIl s’agit d’un poste transversal stratégique où vous serez appelé à interagir avec des collègues de tous nos terminaux maritimes, au Canada et aux États-Unis. 

  0%|          | 0/1 [00:00<?, ?it/s]

Document data: {'_id': 'US', 'Analyste de marché': {'fr': [{'positionTitle': 'Analyste Financier, Goupe Force', 'companyName': 'NFP Corp', 'location': 'California', 'jobType': [], 'description': "Poste en mode hybride 1 à 2 journées au bureau de Montréal ( Langelier)\n\nL’analyste financier sera responsable de l'analyse financière pour fin de la négociation des dossiers, ainsi que de la validation de l'information financière concernant les renouvellements d'assurance collective et les études de marché.\n\nResponsabilités générales\n\n\n\nÉventuelle négociation de renouvellements avec les assureurs;\nAssurer la livraison rapide et réussie des présentations des clients pour les clients potentiels ainsi que les présentations existantes.\nFavoriser un service de haute qualité en appliquant les normes de service à la clientèle, y compris : la création, la mise à jour et le maintien de modèles\nValider les données de l’expérience de renouvellement et de tableaux de taux;\nEntrée de données f

In [21]:
for country in tqdm(positionsDetailsList.keys()):
    for profession in tqdm(positionsDetailsList[country].keys()):
        document_id= country
        collection_name=collection_names[2]
        data={profession:positionsDetailsList[country][profession]}
        try:
            collection = mongo_manager.db[collection_name]
            tmp = mongo_manager.read_single_document(collection_name, document_id)
            for key in data.keys():
                for key2 in data[key].keys():
                    if key in tmp.keys() and key2 in tmp[key].keys() and len(tmp[key][key2])== len(data[key][key2]):
                        print("nothing to update")
                        break
                    if key in tmp.keys() and key2 in tmp[key].keys():
                        tmp[key].extend(data[key])
                    else:
                        if key in tmp.keys():
                            tmp[key] = {}
                        tmp[key] = data[key]       
                collection.update_one({'_id': document_id}, {'$set': tmp})
                print(f'Data updated in {collection_name}/{document_id}')
        except Exception as e:
            print(f'Error updating data in MongoDB: {e}')
        #mongo_manager.update_data_in_mongodb(collection_names[1],country,{profession:positionsDetailsList[country][profession]})

  0%|          | 0/2 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

Document data: {'_id': 'Canada', 'Analyste financière ou analyste financier': {'fr': [{'positionTitle': 'Analyste financier', 'companyName': 'QSL Canada inc.', 'location': 'Ville de Québec, QC•Travail hybride', 'jobType': ['Permanent', ' Temps plein'], 'description': "Poste convoité : Analyste financier\n\nPOSTE ANALYSTE FINANCIER\n\nPartie intégrante de l’équipe des finances et de la comptabilité, vous aurez comme principale responsabilité d’analyser la performance financière et opérationnelle des différentes compagnies, divisions et terminaux du groupe. Vous serez également responsable de concevoir des indicateurs de performance et des rapports pour les différents départements de l’entreprise. Partenaire et expert dans votre domaine, votre travail aura un impact sur le quotidien de nos processus opérationnels et financiers.\n\nIl s’agit d’un poste transversal stratégique où vous serez appelé à interagir avec des collègues de tous nos terminaux maritimes, au Canada et aux États-Unis. 

  0%|          | 0/1 [00:00<?, ?it/s]

Document data: {'_id': 'US', 'Analyste de marché': {'fr': [{'positionTitle': 'Analyste Financier, Goupe Force', 'companyName': 'NFP Corp', 'location': 'California', 'jobType': [], 'description': "Poste en mode hybride 1 à 2 journées au bureau de Montréal ( Langelier)\n\nL’analyste financier sera responsable de l'analyse financière pour fin de la négociation des dossiers, ainsi que de la validation de l'information financière concernant les renouvellements d'assurance collective et les études de marché.\n\nResponsabilités générales\n\n\n\nÉventuelle négociation de renouvellements avec les assureurs;\nAssurer la livraison rapide et réussie des présentations des clients pour les clients potentiels ainsi que les présentations existantes.\nFavoriser un service de haute qualité en appliquant les normes de service à la clientèle, y compris : la création, la mise à jour et le maintien de modèles\nValider les données de l’expérience de renouvellement et de tableaux de taux;\nEntrée de données f

In [23]:
for key in positionsDetailsList.keys():
    for profession in positionsDetailsList[key].keys():
        for language in positionsDetailsList[key][profession].keys():
            print(f"{key} - {profession} - {language} : {len(positionsDetailsList[key][profession][language])}")

Canada - Analyste de marché - fr : 391
Canada - Analyste de marché - en : 1058
US - Analyste de marché - fr : 7
US - Analyste de marché - en : 720
